## Imports

In [ ]:
import pandas as pd
import numpy as np
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem import WordNetLemmatizer
from collections import Counter
from unidecode import unidecode
from gensim.models import Word2Vec
from gensim.models.word2vec import LineSentence
import multiprocessing
from sklearn.feature_extraction.text import TfidfVectorizer
from nltk import sent_tokenize
from transformers import BartForConditionalGeneration, BartTokenizer


ValueError: numpy.ndarray size changed, may indicate binary incompatibility. Expected 88 from C header, got 80 from PyObject

## Dataset

In [2]:
df = pd.read_csv('C:/Users/moreiran/Desktop/projeto_I/B2W-Reviews01.csv')

C:\Users\moreiran\AppData\Local\Temp\ipykernel_23344\631600981.py:1: DtypeWarning: Columns (2) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv('C:/Users/moreiran/Desktop/projeto_I/B2W-Reviews01.csv')


In [3]:
df.head()

submission_date                                        reviewer_id  \
0  2018-01-01 00:11:28  d0fb1ca69422530334178f5c8624aa7a99da47907c44de...   
1  2018-01-01 00:13:48  014d6dc5a10aed1ff1e6f349fb2b059a2d3de511c7538a...   
2  2018-01-01 00:26:02  44f2c8edd93471926fff601274b8b2b5c4824e386ae4f2...   
3  2018-01-01 00:35:54  ce741665c1764ab2d77539e18d0e4f66dde6213c9f0863...   
4  2018-01-01 01:00:28  7d7b6b18dda804a897359276cef0ca252f9932bf4b5c8e...   

  product_id                                       product_name  \
0  132532965  Notebook Asus Vivobook Max X541NA-GO472T Intel...   
1   22562178               Copo Acrílico Com Canudo 500ml Rocie   
2  113022329  Panela de Pressão Elétrica Philips Walita Dail...   
3  113851581               Betoneira Columbus - Roma Brinquedos   
4  131788803  Smart TV LED 43" LG 43UJ6525 Ultra HD 4K com C...   

    product_brand      site_category_lv1       site_category_lv2  \
0             NaN            Informática                Notebook   
1             NaN  Utilidades Domésticas  Copos, Taças e Canecas   
2  philips walita        Eletroportáteis         Panela Elétrica   
3     roma jensen             Brinquedos   Veículos de Brinquedo   
4              lg      TV e Home Theater                      TV   

                       review_title  overall_rating recommend_to_a_friend  \
0                               Bom               4                   Yes   
1  Preço imbatível, ótima qualidade               4                   Yes   
2      ATENDE TODAS AS EXPECTATIVA.               4                   Yes   
3        presente mais que desejado               4                   Yes   
4            Sem duvidas, excelente               5                   Yes   

                                         review_text  reviewer_birth_year  \
0  Estou contente com a compra entrega rápida o ú...               1958.0   
1  Por apenas R$1994.20,eu consegui comprar esse ...               1996.0   
2  SUPERA EM AGILIDADE E PRATICIDADE OUTRAS PANEL...               1984.0   
3  MEU FILHO AMOU! PARECE DE VERDADE COM TANTOS D...               1985.0   
4  A entrega foi no prazo, as americanas estão de...               1994.0   

  reviewer_gender reviewer_state  
0               F             RJ  
1               M             SC  
2               M             SP  
3               F             SP  
4               M             MG

In [4]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 132373 entries, 0 to 132372
Data columns (total 14 columns):
 #   Column                 Non-Null Count   Dtype  
---  ------                 --------------   -----  
 0   submission_date        132373 non-null  object 
 1   reviewer_id            132373 non-null  object 
 2   product_id             132373 non-null  object 
 3   product_name           132289 non-null  object 
 4   product_brand          40982 non-null   object 
 5   site_category_lv1      132367 non-null  object 
 6   site_category_lv2      128360 non-null  object 
 7   review_title           132071 non-null  object 
 8   overall_rating         132373 non-null  int64  
 9   recommend_to_a_friend  132355 non-null  object 
 10  review_text            129098 non-null  object 
 11  reviewer_birth_year    126389 non-null  float64
 12  reviewer_gender        128237 non-null  object 
 13  reviewer_state         128382 non-null  object 
dtypes: float64(1), int64(1), object(12)


Filtrar dataset por um produto específico

In [5]:
df['site_category_lv2'].value_counts()

Smartphone                  17679
TV                           6152
Cabelo                       2544
Notebook                     2468
Acessórios para Celular      2349
                            ...  
Descartáveis para Festa         1
Sem Lactose                     1
Tecidos                         1
Quadrinhos e HQs                1
Literatura Infantil             1
Name: site_category_lv2, Length: 713, dtype: int64

In [6]:
df = df[df['product_name'].str.contains('Smartphone', case=False, na=False)]
df.head()

submission_date                                        reviewer_id  \
7   2018-01-01 01:58:17  e039cbff059effe12756772b358af4323c2157e9561da8...   
13  2018-01-01 03:35:48  1c1d746a5a1b9d0780d0dc0038d827f11658baf703e3fd...   
20  2018-01-01 04:27:44  b6a96310f5f1273a16b798b0d514c740bb96dc85ad93da...   
29  2018-01-01 05:12:13  41d392f391118e768644700aec831e999705dece818326...   
30  2018-01-01 05:17:39  10ddeaa5266cc7558a3cc66d499306bb73379828d2b36b...   

   product_id                                       product_name  \
7   132444092  Smartphone Motorola Moto G 5S Dual Chip Androi...   
13  132444050  Smartphone Motorola Moto G 5S Dual Chip Androi...   
20  125768030  Smartphone LG K10 Dual Chip Android 6.0 Marshm...   
29  125397208  Smartphone Samsung Galaxy A5 2016 Dual Chip An...   
30  132581775  Smartphone Asus Zenfone 4 Selfie Dual Chip And...   

   product_brand        site_category_lv1 site_category_lv2  \
7            NaN  Celulares e Smartphones        Smartphone   
13           NaN  Celulares e Smartphones        Smartphone   
20            lg  Celulares e Smartphones        Smartphone   
29       samsung  Celulares e Smartphones        Smartphone   
30           NaN  Celulares e Smartphones        Smartphone   

                      review_title  overall_rating recommend_to_a_friend  \
7       Gostei bastante do produto               4                   Yes   
13                       Revoltado               1                    No   
20               Gostei do produto               3                   Yes   
29  Mediano com recursos de um top               4                   Yes   
30  Produto ótimo e entrega rápida               5                   Yes   

                                          review_text  reviewer_birth_year  \
7   Produto excelente qualidade boa câmera desenvo...               1987.0   
13  Esse celular não vale nada a bateria não vale ...               1970.0   
20  Produto ofereçe o que prometeu no anúncio, ent...               1986.0   
29  Uma tela impecável. Se sua prioridade é tela e...               1990.0   
30  Aparelho condiz com a sua descrição, super top...               1989.0   

   reviewer_gender reviewer_state  
7                M             GO  
13               M             BA  
20               M             PE  
29               M             PI  
30               M             SP

In [7]:
df = df.dropna(subset=['review_text'])
df.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 16970 entries, 7 to 132351
Data columns (total 14 columns):
 #   Column                 Non-Null Count  Dtype  
---  ------                 --------------  -----  
 0   submission_date        16970 non-null  object 
 1   reviewer_id            16970 non-null  object 
 2   product_id             16970 non-null  object 
 3   product_name           16970 non-null  object 
 4   product_brand          8114 non-null   object 
 5   site_category_lv1      16970 non-null  object 
 6   site_category_lv2      16887 non-null  object 
 7   review_title           16943 non-null  object 
 8   overall_rating         16970 non-null  int64  
 9   recommend_to_a_friend  16970 non-null  object 
 10  review_text            16970 non-null  object 
 11  reviewer_birth_year    16264 non-null  float64
 12  reviewer_gender        16507 non-null  object 
 13  reviewer_state         16532 non-null  object 
dtypes: float64(1), int64(1), object(12)
memory usage: 1.9

## Pre processing dataset strucutre

In [8]:
df.columns

Index(['submission_date', 'reviewer_id', 'product_id', 'product_name',
       'product_brand', 'site_category_lv1', 'site_category_lv2',
       'review_title', 'overall_rating', 'recommend_to_a_friend',
       'review_text', 'reviewer_birth_year', 'reviewer_gender',
       'reviewer_state'],
      dtype='object')

In [9]:
colunas_para_remover = ['product_name', 'submission_date', 'reviewer_id', 'product_id', 'product_brand', 'site_category_lv1', 'site_category_lv2', 'review_title', 'overall_rating', 'recommend_to_a_friend', 'reviewer_birth_year', 'reviewer_gender', 'reviewer_state']

review_text = df.drop(columns=colunas_para_remover)
review_text.head()

review_text
7   Produto excelente qualidade boa câmera desenvo...
13  Esse celular não vale nada a bateria não vale ...
20  Produto ofereçe o que prometeu no anúncio, ent...
29  Uma tela impecável. Se sua prioridade é tela e...
30  Aparelho condiz com a sua descrição, super top...

In [10]:
review_text = review_text.reset_index(drop=True)
review_text.head()

review_text
0  Produto excelente qualidade boa câmera desenvo...
1  Esse celular não vale nada a bateria não vale ...
2  Produto ofereçe o que prometeu no anúncio, ent...
3  Uma tela impecável. Se sua prioridade é tela e...
4  Aparelho condiz com a sua descrição, super top...

In [11]:
review_text.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16970 entries, 0 to 16969
Data columns (total 1 columns):
 #   Column       Non-Null Count  Dtype 
---  ------       --------------  ----- 
 0   review_text  16970 non-null  object
dtypes: object(1)
memory usage: 132.7+ KB


## Pre processing text content

1. Limpeza de texto:

In [36]:
review_text['cleaned_review'] = review_text['review_text'].str.replace(r'<.*?>', '')  # Remove tags HTML
review_text['cleaned_review'] = review_text['cleaned_review'].apply(lambda x: unidecode(x))  # Remove acentos
review_text['cleaned_review'] = review_text['cleaned_review'].str.replace(r'[^a-zA-Z\s]', '')  # Remove caracteres não alfabéticos
# review_text['cleaned_review'] = review_text['cleaned_review'].str.replace(r'[^a-zA-Z\s.,!?]', '') # esse mantem a pontuação
review_text.head()


C:\Users\moreiran\AppData\Local\Temp\ipykernel_23344\2230498947.py:1: FutureWarning: The default value of regex will change from True to False in a future version.
  review_text['cleaned_review'] = review_text['review_text'].str.replace(r'<.*?>', '')  # Remove tags HTML
C:\Users\moreiran\AppData\Local\Temp\ipykernel_23344\2230498947.py:3: FutureWarning: The default value of regex will change from True to False in a future version.
  review_text['cleaned_review'] = review_text['cleaned_review'].str.replace(r'[^a-zA-Z\s]', '')  # Remove caracteres não alfabéticos


review_text  \
0  Produto excelente qualidade boa câmera desenvo...   
1  Esse celular não vale nada a bateria não vale ...   
2  Produto ofereçe o que prometeu no anúncio, ent...   
3  Uma tela impecável. Se sua prioridade é tela e...   
4  Aparelho condiz com a sua descrição, super top...   

                                      cleaned_review  \
0  Produto excelente qualidade boa camera desenvo...   
1  Esse celular nao vale nada a bateria nao vale ...   
2  Produto oferece o que prometeu no anuncio entr...   
3  Uma tela impecavel Se sua prioridade e tela e ...   
4  Aparelho condiz com a sua descricao super top ...   

                                              tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [esse, celular, nao, vale, nada, a, bateria, n...   
2  [produto, oferece, o, que, prometeu, no, anunc...   
3  [uma, tela, impecavel, ., se, sua, prioridade,...   
4  [aparelho, condiz, com, a, sua, descricao, ,, ...   

                                     filtered_tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [celular, nao, vale, nada, bateria, nao, vale,...   
2  [produto, oferece, prometeu, anuncio, ,, entre...   
3  [tela, impecavel, ., prioridade, tela, camera,...   
4  [aparelho, condiz, descricao, ,, super, top, ,...   

                                   normalized_tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [celular, nao, vale, nada, bateria, nao, vale,...   
2  [produto, oferece, prometeu, anuncio, ,, entre...   
3  [tela, impecavel, ., prioridade, tela, camera,...   
4  [aparelho, condiz, descricao, ,, super, top, ,...   

                               normalized_tokens_str  
0  produto excelente qualidade boa camera desenvo...  
1  celular nao vale nada bateria nao vale nada de...  
2  produto oferece prometeu anuncio , entrega rap...  
3  tela impecavel . prioridade tela camera , cara...  
4  aparelho condiz descricao , super top , zen fo...

2. Tokenização

In [37]:
review_text['tokens'] = review_text['cleaned_review'].apply(lambda x: word_tokenize(x.lower()))  # Converte para minúsculas e tokeniza
review_text.head()

review_text  \
0  Produto excelente qualidade boa câmera desenvo...   
1  Esse celular não vale nada a bateria não vale ...   
2  Produto ofereçe o que prometeu no anúncio, ent...   
3  Uma tela impecável. Se sua prioridade é tela e...   
4  Aparelho condiz com a sua descrição, super top...   

                                      cleaned_review  \
0  Produto excelente qualidade boa camera desenvo...   
1  Esse celular nao vale nada a bateria nao vale ...   
2  Produto oferece o que prometeu no anuncio entr...   
3  Uma tela impecavel Se sua prioridade e tela e ...   
4  Aparelho condiz com a sua descricao super top ...   

                                              tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [esse, celular, nao, vale, nada, a, bateria, n...   
2  [produto, oferece, o, que, prometeu, no, anunc...   
3  [uma, tela, impecavel, se, sua, prioridade, e,...   
4  [aparelho, condiz, com, a, sua, descricao, sup...   

                                     filtered_tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [celular, nao, vale, nada, bateria, nao, vale,...   
2  [produto, oferece, prometeu, anuncio, ,, entre...   
3  [tela, impecavel, ., prioridade, tela, camera,...   
4  [aparelho, condiz, descricao, ,, super, top, ,...   

                                   normalized_tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [celular, nao, vale, nada, bateria, nao, vale,...   
2  [produto, oferece, prometeu, anuncio, ,, entre...   
3  [tela, impecavel, ., prioridade, tela, camera,...   
4  [aparelho, condiz, descricao, ,, super, top, ,...   

                               normalized_tokens_str  
0  produto excelente qualidade boa camera desenvo...  
1  celular nao vale nada bateria nao vale nada de...  
2  produto oferece prometeu anuncio , entrega rap...  
3  tela impecavel . prioridade tela camera , cara...  
4  aparelho condiz descricao , super top , zen fo...

3. Remoção de stop words

In [38]:
stop_words = set(stopwords.words('portuguese'))  # Lista de stop words em inglês
review_text['filtered_tokens'] = review_text['tokens'].apply(lambda tokens: [word for word in tokens if word not in stop_words])

In [39]:
review_text.head()

review_text  \
0  Produto excelente qualidade boa câmera desenvo...   
1  Esse celular não vale nada a bateria não vale ...   
2  Produto ofereçe o que prometeu no anúncio, ent...   
3  Uma tela impecável. Se sua prioridade é tela e...   
4  Aparelho condiz com a sua descrição, super top...   

                                      cleaned_review  \
0  Produto excelente qualidade boa camera desenvo...   
1  Esse celular nao vale nada a bateria nao vale ...   
2  Produto oferece o que prometeu no anuncio entr...   
3  Uma tela impecavel Se sua prioridade e tela e ...   
4  Aparelho condiz com a sua descricao super top ...   

                                              tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [esse, celular, nao, vale, nada, a, bateria, n...   
2  [produto, oferece, o, que, prometeu, no, anunc...   
3  [uma, tela, impecavel, se, sua, prioridade, e,...   
4  [aparelho, condiz, com, a, sua, descricao, sup...   

                                     filtered_tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [celular, nao, vale, nada, bateria, nao, vale,...   
2  [produto, oferece, prometeu, anuncio, entrega,...   
3  [tela, impecavel, prioridade, tela, camera, ca...   
4  [aparelho, condiz, descricao, super, top, zen,...   

                                   normalized_tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [celular, nao, vale, nada, bateria, nao, vale,...   
2  [produto, oferece, prometeu, anuncio, ,, entre...   
3  [tela, impecavel, ., prioridade, tela, camera,...   
4  [aparelho, condiz, descricao, ,, super, top, ,...   

                               normalized_tokens_str  
0  produto excelente qualidade boa camera desenvo...  
1  celular nao vale nada bateria nao vale nada de...  
2  produto oferece prometeu anuncio , entrega rap...  
3  tela impecavel . prioridade tela camera , cara...  
4  aparelho condiz descricao , super top , zen fo...

4. Normalização

In [40]:
review_text['normalized_tokens'] = review_text['filtered_tokens'].apply(lambda tokens: [word.lower() for word in tokens])

In [41]:
review_text.head()

review_text  \
0  Produto excelente qualidade boa câmera desenvo...   
1  Esse celular não vale nada a bateria não vale ...   
2  Produto ofereçe o que prometeu no anúncio, ent...   
3  Uma tela impecável. Se sua prioridade é tela e...   
4  Aparelho condiz com a sua descrição, super top...   

                                      cleaned_review  \
0  Produto excelente qualidade boa camera desenvo...   
1  Esse celular nao vale nada a bateria nao vale ...   
2  Produto oferece o que prometeu no anuncio entr...   
3  Uma tela impecavel Se sua prioridade e tela e ...   
4  Aparelho condiz com a sua descricao super top ...   

                                              tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [esse, celular, nao, vale, nada, a, bateria, n...   
2  [produto, oferece, o, que, prometeu, no, anunc...   
3  [uma, tela, impecavel, se, sua, prioridade, e,...   
4  [aparelho, condiz, com, a, sua, descricao, sup...   

                                     filtered_tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [celular, nao, vale, nada, bateria, nao, vale,...   
2  [produto, oferece, prometeu, anuncio, entrega,...   
3  [tela, impecavel, prioridade, tela, camera, ca...   
4  [aparelho, condiz, descricao, super, top, zen,...   

                                   normalized_tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [celular, nao, vale, nada, bateria, nao, vale,...   
2  [produto, oferece, prometeu, anuncio, entrega,...   
3  [tela, impecavel, prioridade, tela, camera, ca...   
4  [aparelho, condiz, descricao, super, top, zen,...   

                               normalized_tokens_str  
0  produto excelente qualidade boa camera desenvo...  
1  celular nao vale nada bateria nao vale nada de...  
2  produto oferece prometeu anuncio , entrega rap...  
3  tela impecavel . prioridade tela camera , cara...  
4  aparelho condiz descricao , super top , zen fo...

5. Remoção de duplicatas

In [42]:
review_text['normalized_tokens_str'] = review_text['normalized_tokens'].apply(lambda tokens: ' '.join(tokens))
review_text = review_text.drop_duplicates(subset=['normalized_tokens_str'])

In [43]:
review_text.head()

review_text  \
0  Produto excelente qualidade boa câmera desenvo...   
1  Esse celular não vale nada a bateria não vale ...   
2  Produto ofereçe o que prometeu no anúncio, ent...   
3  Uma tela impecável. Se sua prioridade é tela e...   
4  Aparelho condiz com a sua descrição, super top...   

                                      cleaned_review  \
0  Produto excelente qualidade boa camera desenvo...   
1  Esse celular nao vale nada a bateria nao vale ...   
2  Produto oferece o que prometeu no anuncio entr...   
3  Uma tela impecavel Se sua prioridade e tela e ...   
4  Aparelho condiz com a sua descricao super top ...   

                                              tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [esse, celular, nao, vale, nada, a, bateria, n...   
2  [produto, oferece, o, que, prometeu, no, anunc...   
3  [uma, tela, impecavel, se, sua, prioridade, e,...   
4  [aparelho, condiz, com, a, sua, descricao, sup...   

                                     filtered_tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [celular, nao, vale, nada, bateria, nao, vale,...   
2  [produto, oferece, prometeu, anuncio, entrega,...   
3  [tela, impecavel, prioridade, tela, camera, ca...   
4  [aparelho, condiz, descricao, super, top, zen,...   

                                   normalized_tokens  \
0  [produto, excelente, qualidade, boa, camera, d...   
1  [celular, nao, vale, nada, bateria, nao, vale,...   
2  [produto, oferece, prometeu, anuncio, entrega,...   
3  [tela, impecavel, prioridade, tela, camera, ca...   
4  [aparelho, condiz, descricao, super, top, zen,...   

                               normalized_tokens_str  
0  produto excelente qualidade boa camera desenvo...  
1  celular nao vale nada bateria nao vale nada de...  
2  produto oferece prometeu anuncio entrega rapid...  
3  tela impecavel prioridade tela camera cara pon...  
4  aparelho condiz descricao super top zen fone c...

## Join the texts

In [44]:
join_text = ''.join(review_text['normalized_tokens_str'])
join_text

'produto excelente qualidade boa camera desenvolvimento android rapidezcelular nao vale nada bateria nao vale nada descarrega sozinha usando esquenta tanto faz medo espludi pior compra vida condicoes quebrava mil pedacos comprava outro qualquer marca menos motorolaproduto oferece prometeu anuncio entrega rapida bem antes prazotela impecavel prioridade tela camera cara ponto fraco fica conta armazenamento apenas gb camera frontal apenas mpixels flash entanto camera principal mpixels perfeitaaparelho condiz descricao super top zen fone comprei esposa amando super recomendotop linha vale pena comprar gostei nao arrependo ter compradomelhor custo beneficio exatamente anunciado recomendogostaria saber celular camera frontalachei lindo too linha design lindo camera resposta boa rapida preco prazo tudo certinhoadorei celularparabens americanasnota dezaparelho otima qualidade defeitos entrega pontualidade qualidadecamera frontal terrivel tanto faz ta claro escuro foto fica ruim qualquer jeito 

In [45]:
len(join_text)

1757809

In [46]:
caminho_arquivo_txt = "texto_unido.txt"

# Abra o arquivo em modo de escrita e escreva o texto unido nele
with open(caminho_arquivo_txt, 'w', encoding='utf-8') as arquivo_txt:
    arquivo_txt.write(join_text)

## Corpus

In [47]:
corpus_path = "C:/Users/moreiran/Desktop/projeto_I/texto_unido.txt"

Vetorização:

In [48]:
# Carregue o texto e tokenize as sentenças
with open(corpus_path, "r", encoding="utf-8") as file:
    sentences = [line.strip().split() for line in file]

In [49]:
# Treine o modelo Word2Vec
# Ajuste os hiperparâmetros conforme necessário para o seu conjunto de dados.
model = Word2Vec(
    sentences,
    vector_size=100,  # Dimensão dos vetores de palavras
    window=5,         # Janela de contexto
    min_count=5,      # Frequência mínima de palavras a serem consideradas
    workers=multiprocessing.cpu_count(),  # Número de núcleos da CPU a serem usados
)

# Salvar o modelo treinado
model.save("word2vec_model")

# Carregar o modelo treinado
model = Word2Vec.load("word2vec_model")


In [50]:
word = "produto"  # Substitua "apple" pela palavra que você deseja consultar.

# Obter o vetor da palavra
word_vector = model.wv[word]

# Encontrar palavras similares
similar_words = model.wv.most_similar(word, topn=5)

print(f"Vetor da palavra '{word}':")
print(word_vector)
print(f"Palavras similares a '{word}':")
for similar_word, score in similar_words:
    print(f"{similar_word}: {score}")

Vetor da palavra 'produto':
[-0.16275358  0.3413468   0.04727431  0.02673246  0.10259256 -0.52686363
  0.11107258  0.63691914 -0.13120204 -0.18298303 -0.01957331 -0.34918606
 -0.14599942  0.19243462  0.03356095 -0.15898731  0.10163158 -0.23179542
  0.05086143 -0.57482177  0.20938727  0.12147287  0.14782129 -0.14335606
 -0.00951357 -0.04196209 -0.18976064 -0.12531196 -0.11692166  0.1302558
  0.3218574  -0.01975276  0.23200198 -0.2985487  -0.08980308  0.23275395
  0.04612944 -0.07322068 -0.1198497  -0.4841306   0.0343916  -0.2552205
 -0.18668136 -0.07666373  0.1932677  -0.05877259 -0.26220238 -0.04685973
  0.08432537  0.12779652  0.14258218 -0.2563428  -0.08601011  0.01104549
 -0.26486817  0.09995842  0.08493602 -0.0814417  -0.34192634  0.16006061
 -0.00328246  0.04559861 -0.01366281 -0.02689819 -0.3100077   0.2651951
  0.15294962  0.21240091 -0.3257797   0.29967564 -0.20098044  0.15600649
  0.34901172 -0.09350822  0.33374372  0.01813267 -0.04690461 -0.01214105
 -0.16554242  0.08136325 -

## Ranking: most important sentences
Essa parte ta dando problema, preciso ver como melhorar

In [51]:
# ler o arquivo de texto
with open("texto_unido.txt", "r", encoding="utf-8") as file:
    text = file.read()

In [52]:
# dividir o texto em sentenças
sentences = sent_tokenize(text)

In [53]:
# calcular a importância das sentenças

#TODO: como escolher essas keywords?

keywords = ["produto", "qualidade", "recomendo"]  # Substitua com suas palavras-chave reais.

# Calcule a importância de cada sentença com base na contagem de palavras-chave
sentence_importance = []
for sentence in sentences:
    importance = sum(1 for keyword in keywords if keyword in sentence.lower())
    sentence_importance.append(importance)

In [54]:
# Classifique as sentenças com base em sua importância e selecione um número desejado de sentenças para compor o resumo.

num_sentences_in_summary = 3  # Defina o número de sentenças desejado.

# Selecione as sentenças mais importantes
summary_sentences = [sentences[i] for i in sorted(range(len(sentences)), key=lambda i: sentence_importance[i], reverse=True)[:num_sentences_in_summary]]

In [55]:
print(summary_sentences[0])

produto excelente qualidade boa camera desenvolvimento android rapidezcelular nao vale nada bateria nao vale nada descarrega sozinha usando esquenta tanto faz medo espludi pior compra vida condicoes quebrava mil pedacos comprava outro qualquer marca menos motorolaproduto oferece prometeu anuncio entrega rapida bem antes prazotela impecavel prioridade tela camera cara ponto fraco fica conta armazenamento apenas gb camera frontal apenas mpixels flash entanto camera principal mpixels perfeitaaparelho condiz descricao super top zen fone comprei esposa amando super recomendotop linha vale pena comprar gostei nao arrependo ter compradomelhor custo beneficio exatamente anunciado recomendogostaria saber celular camera frontalachei lindo too linha design lindo camera resposta boa rapida preco prazo tudo certinhoadorei celularparabens americanasnota dezaparelho otima qualidade defeitos entrega pontualidade qualidadecamera frontal terrivel tanto faz ta claro escuro foto fica ruim qualquer jeito a

In [56]:
# exibir o resumo
summary = " ".join(summary_sentences)
print(summary)

produto excelente qualidade boa camera desenvolvimento android rapidezcelular nao vale nada bateria nao vale nada descarrega sozinha usando esquenta tanto faz medo espludi pior compra vida condicoes quebrava mil pedacos comprava outro qualquer marca menos motorolaproduto oferece prometeu anuncio entrega rapida bem antes prazotela impecavel prioridade tela camera cara ponto fraco fica conta armazenamento apenas gb camera frontal apenas mpixels flash entanto camera principal mpixels perfeitaaparelho condiz descricao super top zen fone comprei esposa amando super recomendotop linha vale pena comprar gostei nao arrependo ter compradomelhor custo beneficio exatamente anunciado recomendogostaria saber celular camera frontalachei lindo too linha design lindo camera resposta boa rapida preco prazo tudo certinhoadorei celularparabens americanasnota dezaparelho otima qualidade defeitos entrega pontualidade qualidadecamera frontal terrivel tanto faz ta claro escuro foto fica ruim qualquer jeito a

In [57]:
# não sei pq meu note não ta printando 
# então vou salvar o resumo em txt pra visualizar 
caminho_arquivo_resumo = "resumo.txt"

# Abra o arquivo para escrita e salve o resumo
with open(caminho_arquivo_resumo, "w", encoding="utf-8") as arquivo:
    arquivo.write(summary)


In [58]:
len(summary)

1757809

## Summariza big text

In [59]:
# Carregue o modelo e o tokenizador
model_name = "facebook/bart-large-cnn"
tokenizer = BartTokenizer.from_pretrained(model_name)
model = BartForConditionalGeneration.from_pretrained(model_name)

# Texto a ser resumido
with open("texto_unido.txt", "r", encoding="utf-8") as file:
    text = file.read()

# Pré-processamento do texto
input_ids = tokenizer.encode(text, return_tensors="pt", max_length=1024, truncation=True)

# Gere o resumo
summary_ids = model.generate(input_ids, max_length=150, min_length=40, num_beams=4, length_penalty=2.0, early_stopping=True)

# Decodifique o resumo
summary = tokenizer.decode(summary_ids[0], skip_special_tokens=True)

# Imprima o resumo
print("Resumo:")
print(summary)


Resumo:
produto excelente qualidade boa camera desenvolvimento android rapidezcelular nao vale nada bateria nao nada descarrega sozinha usando esquenta tanto faz medo espludi pior compra vida.
